<img src="pic/ex06.png" width="100%"> <br>

<h1 class="jp-toc-ignore">ICON Training - Hands-on Session</h1>

# Exercise 6.1: ICON ComIn, Part I

---
The **ICON Community Interface (ComIn)** enables the integration of **plugins** which is a flexible way to extend the code with your own routines and variables at run-time.  
ComIn offers the opportunity to write your plugins in various programming languages, including Fortran, C, and Python. In this training course, we will focus on developing **Python plugins**.
* **Step P1**: We repeat the previous task "Step F1", this time using only a few lines of Python code.
* **Step P2**: We learn how to perform data MPI gathering.
* **Step P3**: In the final step, we learn how to use the coupling library [YAC](https://dkrz-sw.gitlab-pages.dkrz.de/yac/) in a plugin to interpolate fields from the ICON unstructured grid onto a custom lat-lon grid, and then visualize the interpolated fields.

To complete the following exercises, it is important to have a basic understanding of programming in Python, particularly the correct use of indentation.

<br/>

<div style="width:100%;height:120px;border-top: 2px solid darkgray;border-bottom: 2px solid darkgray;padding: 10px 0px 10px 0px">
<img src="pic/logo_comin.png" style="float:right;height:120px">
</div>

## Preliminary Step: Building the ICON ComIn Python Adapter

We will use a prebuilt ICON binary in `ICONDIR=/pool/data/ICON/ICON_training/icon`. As you are writing a Python plugin in this exercise, there is **no** need to compile the ICON code at any stage to complete the task.  

For **educational purposes**, it is demonstrated below how to build ICON in a way that allows it to run ComIn plugins.
We outline the steps for creating an out-of-source build (recommended).

```bash
mkdir -p icon/build
cd icon/build
../config/dkrz/levante.gcc \
  --enable-comin --enable-bundled-python=comin
make -j6

**Remarks**
- The `--enable-bundled-python=comin` configuration option is used to build the ComIn Python adapter. This adapter is a dynamic library and can be found under `/build/externals/comin/build/plugins/python_adapter/libpython_adapter.so`
- This is the minimal configuration setting for ComIn. For the full, `YAC` enabled version, please refer back to the <a href="../exercise_programming/icon_exercise_programming.ipynb">explanation provided for F1</a>.

## Step P1: Writing a ComIn Python Plugin

For the necessary information on ComIn, please refer to Section 9.5 of the ICON tutorial. In addition, the ComIn project website contains more detailed documentation. The ICON documentation website contains a section on ComIn featuring the documentation for the latest release version. All these references can be found at the end of this Jupyter notebook.  

### Your First ComIn Plugin

In this step, rather than implementing your programming directly into the ICON source code, you will develop a **ComIn plugin** to perform a task similar to **Step F1** in the ICON programming exercise. In other words, we will visualise ICON's domain decomposition.

<figure >
<img src="pic/EP.svg"  width="100%">
</figure>
This figure provides a schematic overview of the available entry points in the ICON source code: The different loops of the time stepping scheme (dynamics, fast and slow physics) can be supplemented by attached plugin functions, with the locations marked by the red arrows.

<br/>

<div class="alert alert-success">
  <b style="color:#2d4b9b;">Exercise:</b> 
  We will write a Python script (ComIn plugin). To this end, start from an (almost) empty <code>scripts/comin_plugin_P1.py</code>, which you can open by clicking <a href="scripts/comin_plugin_P1.py">here</a>.
  In your plugin, add a 2D diagnostic variable named <code>comin_process_id</code> for domain 1.
  
 As outlined in the ICON tutorial, adding a new variable in your ComIn plugin involves two steps:
 <ul>
  <li>First you need to <b>register a new variable</b> and set the required metadata for the new variable. <br/>
      You will need the library command <code>comin.var_request_add</code> for this.
      For a list of available metadata, refer to the <a href="https://icon-comin.gitlab-pages.dkrz.de/comin/d7/de6/md__2builds_2icon-comin_2comin_2doc_2comin__python__api.html">Python API</a>.</li>
    
  <li>Secondly, you should <b>access your registered variable</b> like any other ICON variable within the secondary constructor of your plugin. <br/>
      This happens with the API function <code>comin.var_get</code>.
      Furthermore, you will need to specify the entry point for your callback function. In this exercise, we will use the <code>EP_ATM_WRITE_OUTPUT_BEFORE</code> entry point. </li>   
  </ul>
</div>

<details>
<summary style="font-size: 1.1em;">Solution</summary><br/>

```python
import comin

jg = 1  # set the domain id

# request to register the variable
var_descriptor = ("comin_process_id", jg)
comin.var_request_add(var_descriptor, lmodexclusive=False)
comin.metadata_set(var_descriptor, zaxis_id = comin.COMIN_ZAXIS_2D)


@comin.EP_SECONDARY_CONSTRUCTOR
def simple_python_constructor():
    global comin_process_id
    comin_process_id = comin.var_get([comin.EP_ATM_WRITE_OUTPUT_BEFORE], 
                                     ("comin_process_id", jg), 
                                     flag=comin.COMIN_FLAG_WRITE
                                    )
```

</details>

### Filling the data array with the process ID 

<div class="alert alert-success">
  <b style="color:#2d4b9b;">Exercise:</b> 
Write a callback function in your plugin <a href="scripts/comin_plugin_P1.py"><code>scripts/comin_plugin_P1.py</code></a> and attach it to the <code>EP_ATM_WRITE_OUTPUT_BEFORE</code> entry point. 
This is done using the <code>comin.register_callback</code> function (a function decorator).
<p/>
In the callback function, fill the variable <code>comin_process_id</code> with the MPI rank of the processor. 
</div>


**Hints:**
* In the callback function, import the NumPy package and use `numpy.asarray` to convert a variable handle you accessed into a NumPy array.
* Refer to the Python API description for ICON ComIn to learn how to obtain the MPI rank of the ICON model in your plugin. A link to the API description is provided in the References section at the end of this Jupyter notebook.<br/>
  You should use ComIn's so-called **host MPI communicator** which is the MPI communicator that comprises all MPI tasks of the ICON simulation which are involved in the ComIn callbacks.
* If you want to add a log message to your plugin script, you should use <code>print("...", file=sys.stderr)</code> to avoid buffering.


<div class="alert alert-info">
<b>Remark:</b> Actually, the use of <code>np.asarray</code> is an important point to note: The `comin.var_get` call returns a handle to an ICON variable. However, since ICON contains fields with multiple time levels, the corresponding array pointer changes during the model run. Each time the plugin needs to access the array (pointer), it must be explicitly or implicitly converted to a NumPy array.
</div>

<details>
<summary style="font-size: 1.1em;">Solution</summary><br/>

```python
@comin.EP_ATM_WRITE_OUTPUT_BEFORE
def simple_python_callbackfct():
    import numpy as np
    # print("simple_python_callbackfct called!", file=sys.stderr)
    comin_process_id_np = np.asarray(comin_process_id)
    comin_process_id_np[:] = comin.parallel_get_host_mpi_rank()
```

</details>

### Running the ICON Model

Now that you've finished writing your plugin, the next step is to run the ICON model.
First, execute the following cell in order to set up an example ICON job, similar to the ICON-LAM setting of the previous exercise.

In [ ]:
import os
import subprocess

user = os.environ['USER']
home = os.environ['HOME']
scratchdir = f"/scratch/{user[0]}/{user}"
icondir = f"/pool/data/ICON/ICON_training/icon"
expdir = f"{scratchdir}/exercise_comin/P1"
%env ICONDIR={icondir}
%env EXPDIR={expdir}
%env SCRATCHDIR={scratchdir}

Run setup script

In [ ]:
!bash $HOME/icon-training-scripts/exercise_comin/prepared/prepare_icon_run.sh

Plugins are enabled via a special namelist `comin_nml`.
In order to load your plugin dynamically while ICON is running, add a `comin_nml` namelist to the ICON namelist file. To this end, execute the cell below. We set the `plugin_library = libpython_adapter.so` with its absolute path such that it can be found by ICON and the operating system.

*Note: Alternatively, the search path for `libpython_adapter.so` could be set through the environment variable `LD_LIBRARY_PATH`.*

In [ ]:
# Append comin_nml block
with open(f"{expdir}/NAMELIST_ICON", 'a') as f:
    f.write(f"""&comin_nml
   plugin_list(1)%name           = "comin_plugin"
   plugin_list(1)%plugin_library = "{icondir}/build/externals/comin/build/plugins/python_adapter/libpython_adapter.so"
   plugin_list(1)%options        = "{home}/icon-training-scripts/exercise_comin/scripts/comin_plugin_P1.py"
/
""")

We must customize `NAMELIST_ICON` to ensure that `comin_process_id` is included in the model output files for the first domain. 

In [ ]:
# Append comin_nml block
with open(f"{expdir}/NAMELIST_ICON", 'a') as f:
    f.write(f"""&output_nml
 filetype                    = 4                     ! netcdf
 dom                         = 1
 output_bounds               = 0., 10000000., 3600.  ! start, end, increment
 steps_per_file              = 1
 mode                        = 1
 include_last                = .FALSE.
 steps_per_file_inclfirst    = .FALSE.
 output_filename             = 'NWP_LAM'
 filename_format             = '<output_filename>_DOM<physdom>_<datetime2>'
 output_grid                 = .FALSE.
 remap                       = 1                     ! 1: remap to lat-lon grid
 reg_lon_def                 = 0.8,0.1,17.2
 reg_lat_def                 = 43.9,0.1,57.7
 ml_varlist                  = "comin_process_id"
/
""")

The other parts of the Fortran namelist remain unchanged. In the run script, we set up the environment variables and create symbolic links to the necessary input data required for running the ICON experiment in a directory with plenty of space (`scratch`).

Now you can run the ICON model.

In [ ]:
!cd $EXPDIR && sbatch --account=$SLURM_JOB_ACCOUNT --export=ICONDIR $EXPDIR/icon-lam.sbatch

In [ ]:
!squeue -u $USER

<table border="0" cellspacing="0" cellpadding="0" style="width:100%; border-collapse:collapse;">
  <tr>
    <td style="vertical-align:top; padding-right:24px;">
      <div class="alert alert-success">
        <b style="color:#2d4b9b;">Exercise:</b> 
        <ul>
          <li>
            Use the <a href="../exercise_programming/scripts/icon_exercise_programming_plot01.ipynb">plot script</a> from Step F1 to visualize <code>comin_process_id</code>.<br/>
            Your result should look like the plot on the right.
          </li>
        </ul>
      </div>
    </td>
    <td style="vertical-align:top; text-align:right;">
      <figure>
        <img src="reference/P1_comin_plugin/domain_decomp_p1.png" width="600" style="display:block;">
        <figcaption style="text-align:center"><em>Reference solution for "Step P1: Writing a ComIn Python Plugin".</em></figcaption>
      </figure>
    </td>
  </tr>
</table>


---

<h2 class="jp-toc-ignore"> <b style="color:#2d4b9b;"><b style="color:#2d4b9b;"> Congratulations! You have successfully completed Exercise 6, Part I.</b></h2>

---

## Further Reading and Resources

<ul>
<li>
  ICON Tutorial, Ch. 9: <a href="https://www.dwd.de/DE/leistungen/nwv_icon_tutorial/nwv_icon_tutorial.html">https://www.dwd.de/DE/leistungen/nwv_icon_tutorial/nwv_icon_tutorial.html</a>  
    <br/>A new <b>draft version</b> of the ICON Tutorial is available here: <a href="https://icon-training-2025-scripts-rendering-cc74a6.gitlab-pages.dkrz.de/index.html">https://icon-training-2025-scripts-rendering-cc74a6.gitlab-pages.dkrz.de/index.html</a>. It is currently being finalized and will be published soon.
</li>
<li>
  Documentation on the ICON ComIn project website: <a href="https://gitlab.dkrz.de/icon-comin/comin/-/blob/master/doc/icon_comin_doc.md?ref_type=heads">https://gitlab.dkrz.de/icon-comin/comin/-/blob/master/doc/icon_comin_doc.md?ref_type=heads</a>  
</li>
<li>
  Python API description for ICON ComIn: <a href="https://gitlab.dkrz.de/icon-comin/comin/-/blob/master/doc/comin_python_api.md?ref_type=head">https://gitlab.dkrz.de/icon-comin/comin/-/blob/master/doc/comin_python_api.md?ref_type=head</a>  
</li>
<li> 
 ICON Documentaton website: Information on ComIn, including the current user guide:
 <a href="https://docs.icon-model.org/tools/comin/comin.html">https://docs.icon-model.org/tools/comin/comin.html</a>
</li>
</ul>

---

*Author info: Deutscher Wetterdienst (DWD) 2025 ::  icon@dwd.de. For a full list of contributors, see CONTRIBUTING in the root directory. License info: see LICENSE file.*